In [12]:
import pycolmap
from pathlib import Path
import shutil
import urllib.request
import zipfile
import io
import matplotlib.pyplot as plt
from PIL import Image
import numpy as np
from mpl_toolkits.mplot3d import Axes3D
import plotly.graph_objects as go

In [2]:
def plot_cameras(reconstrucao):

    fig = plt.figure(figsize=(10, 8))
    ax = fig.add_subplot(111, projection='3d')

    for image_id, image in reconstruction.images.items():
        #Posição da câmera
        cam_fromworld = image.cam_from_world()
        camera_pos = cam_fromworld.translation
        ax.scatter(camera_pos[0], camera_pos[1], camera_pos[2], c='red', marker='o')

        # Calcula a orientação da câmera
        rotation_matrix = cam_fromworld.rotation.matrix()
        forward_dir = rotation_matrix @ np.array([0, 0, 1])  # Vetor forward da câmera
        ax.quiver(
            camera_pos[0], camera_pos[1], camera_pos[2],
            forward_dir[0], forward_dir[1], forward_dir[2],
            length=0.1, color='blue', arrow_length_ratio=0.1
        )

    ax.set_xlabel('X')
    ax.set_ylabel('Y')
    ax.set_zlabel('Z')
    ax.set_title('Camera Positions and Directions')
    plt.show()

In [10]:
def vis_estatica_camera_objeto(reconstruction):
    points_3d = []
    
    for point3D_id, point3D in reconstruction.points3D.items():
        points_3d.append(point3D.xyz)  

    points_3d = np.array(points_3d)  

    fig = plt.figure(figsize=(10, 8))
    ax = fig.add_subplot(111, projection='3d')

    ax.scatter(
        points_3d[:,0],  # X
        points_3d[:,1],  # Y
        points_3d[:,2],  # Z
        s=1,  
        c='blue',  
        alpha=0.5,  
        label="Estimated Object"
    )

    camera_plotted = False
    for image in reconstruction.images.values():
        cam_fromworld=image.cam_from_world()
        cam_pos=cam_fromworld.translation
        if not camera_plotted:
            ax.scatter(cam_pos[0], cam_pos[1], cam_pos[2], c='red', marker='^', label="Camera")
            camera_plotted = True
        else:
            ax.scatter(cam_pos[0], cam_pos[1], cam_pos[2], c='red', marker='^')

    ax.set_xlabel('X')
    ax.set_ylabel('Y')
    ax.set_zlabel('Z')

    ax.legend(bbox_to_anchor=(1.05, 1), loc='upper left')

    plt.title("Estimated Object + Camera")
    plt.tight_layout()  
    plt.show()

In [15]:
def vis_interativa_camera_objeto(reconstruction):

    points_3d = []
    
    for point3D_id, point3D in reconstruction.points3D.items():
        points_3d.append(point3D.xyz)  

    points_3d = np.array(points_3d)
    
    cam_x_coords, cam_y_coords, cam_z_coords = [], [], []

    for image in reconstruction.images.values():
        cam_fromworld = image.cam_from_world()
        cam_pos = cam_fromworld.translation

        cam_x_coords.append(cam_pos[0])
        cam_y_coords.append(cam_pos[1])
        cam_z_coords.append(cam_pos[2])

    fig = go.Figure()
    fig.add_trace(
        go.Scatter3d(
            x=points_3d[:, 0],
            y=points_3d[:, 1],
            z=points_3d[:, 2],
            mode='markers',
            marker=dict(size=1.5, color='blue', opacity=0.6),
            name='Estimated Object'))

    fig.add_trace(
        go.Cone(
            x=cam_x_coords, y=cam_y_coords, z=cam_z_coords,
            u=-np.array(cam_x_coords), v=-np.array(cam_y_coords), w=-np.array(cam_z_coords),
            sizemode="absolute", sizeref=20, anchor="tip",
            colorscale='Reds', showscale=False, name='Camera',
            showlegend=True))

    fig.update_layout(
        title_text="Visualização da Nuvem Esparsa 3D",
        scene=dict(
            xaxis_title='X',
            yaxis_title='Y',
            zaxis_title='Z',
            aspectratio=dict(x=1, y=1, z=1)
        ),
        margin=dict(l=0, r=0, b=0, t=40),
        showlegend=True,
        legend=dict(
            x=0.8,
            y=0.9,
            xanchor='center',
            yanchor='top',
            bgcolor='rgba(255, 255, 255, 0.7)',
            bordercolor='rgba(0, 0, 0, 0.5)',
            borderwidth=1
        )
    )

    fig.show()

In [16]:

grupos_imagens = ['Imagens1', 'Imagens2', 'Imagens3', 'Imagens4']

CAMERA = False
METRICAS = True
VIS_ESTATICA = False
VIS_INTERATIVA = True

for conjunto_imagens in grupos_imagens:
    project_path = Path(f'Resultados/{conjunto_imagens}/colmap_project')
    database_path = project_path / 'database.db'
    output_path = project_path / 'sparse/0'
    #image_path = Path(f'imagens-t2/{conjunto_imagens}')
    
    reconstruction = pycolmap.Reconstruction(output_path) 
    
    print(f'=============={conjunto_imagens}==============')

    if CAMERA:
        plot_cameras(reconstruction)
    
    if METRICAS:
        reprojection_errors = np.array([point3D.error for point3D in reconstruction.points3D.values()])
        mean_reprojection_error = np.mean(reprojection_errors)
        median_reprojection_error = np.median(reprojection_errors)
        num_sparse_points = len(reconstruction.points3D)
        
        print(f"Número de Pontos Esparsos: {num_sparse_points}")
        print(f"Erro de Reprojeção Médio: {mean_reprojection_error:.4f} pixels")
        print(f"Erro de Reprojeção Mediano: {median_reprojection_error:.4f} pixels \n")
    
    if VIS_ESTATICA:
        vis_estatica_camera_objeto(reconstruction)

    if VIS_INTERATIVA:
        vis_interativa_camera_objeto(reconstruction)

==============Imagens1==============
Número de Pontos Esparsos: 77204
Erro de Reprojeção Médio: 0.9534 pixels
Erro de Reprojeção Mediano: 0.8952 pixels 



==============Imagens2==============
Número de Pontos Esparsos: 2218
Erro de Reprojeção Médio: 1.0895 pixels
Erro de Reprojeção Mediano: 1.0298 pixels 



==============Imagens3==============
Número de Pontos Esparsos: 22789
Erro de Reprojeção Médio: 1.0339 pixels
Erro de Reprojeção Mediano: 0.9830 pixels 



==============Imagens4==============
Número de Pontos Esparsos: 34347
Erro de Reprojeção Médio: 0.8630 pixels
Erro de Reprojeção Mediano: 0.7668 pixels 

